Create a stored procedure to get the common queries between the baseline and target clusters.

In [0]:
CREATE OR REPLACE PROCEDURE common_queries_sp(baseline_identifier varchar(500), target_identifier varchar(500))
AS $$
DECLARE 
 my_sql varchar(8000);
 baseline_identifier1 varchar(500);
 target_identifier1 varchar(500);
BEGIN
 baseline_identifier1 := '''' + baseline_identifier + '''';
 target_identifier1 := '''' + target_identifier + '''';

 my_sql :=
 'CREATE OR REPLACE VIEW common_queries AS(
    WITH
    baseline as 
    (
    SELECT *
    FROM comparison_stats.redshift_config_comparision_aggregate
    WHERE cluster_identifier = '+ baseline_identifier1 + '
    and query_text like ''%replay%''
    ),
    target as (
    SELECT *
    FROM comparison_stats.redshift_config_comparision_aggregate
    WHERE cluster_identifier = ' + target_identifier1 + '
    and query_text like ''%replay%''
    )
    SELECT
    split_part(split_part(baseline.query_text,''}'',1),''"'', 4) source_xid,
    TRIM('', '' FROM TRIM('': '' FROM split_part(split_part(baseline.query_text,''}'',1),''"'', 7))) source_idx,
    baseline.query_label query_label,
    baseline.query_type query_type,
    baseline.username,
    CASE WHEN split_part(baseline.query_text,''*/ '',2) != '''' THEN split_part(baseline.query_text,''*/ '',2) ELSE baseline.query_text END as querytxt,
    baseline.query_text as source_querytxt,

    split_part(split_part(baseline.query_text,''}'',1),''"'', 10) baseline_replaystart,
    baseline.execution_time as baseline_exec,
    baseline.elapsed_time as baseline_query,
    baseline.queue_time as baseline_queue,
    baseline.compile_time as baseline_compile,
    baseline.query_id baseline_query_id,
    baseline.transaction_id baseline_transaction_id,
    baseline.session_id baseline_session_id,
    baseline.status as baseline_aborted,
    baseline.start_time as baseline_starttime,
    baseline.end_time as baseline_endtime,
    baseline.result_cache_hit as baseline_cache_hit,

    split_part(split_part(target.query_text,''}'',1),''"'', 10) target_replaystart,
    target.execution_time as target_exec,
    target.elapsed_time as target_query,
    target.queue_time as target_queue,
    target.compile_time as target_compile,
    target.query_id target_query_id,
    target.transaction_id target_transaction_id,
    target.session_id target_session_id,
    target.status as target_aborted,
    target.start_time as target_starttime,
    target.end_time as target_endtime,
    target.result_cache_hit as target_cache_hit
    
    FROM baseline
    JOIN target
    ON split_part(split_part(TRIM(baseline.query_text),''}'',1),''"'', 4) = split_part(split_part(TRIM(target.query_text),''}'',1),''"'', 4) 
    AND TRIM('', '' FROM TRIM('': '' FROM split_part(split_part(TRIM(baseline.query_text),''}'',1),''"'', 7))) = 
    TRIM('', '' FROM TRIM('': '' FROM split_part(split_part(TRIM(target.query_text),''}'',1),''"'', 7)))
    AND split_part(TRIM(baseline.query_text),''*/ '',2) = split_part(TRIM(target.query_text),''*/ '',2)
    WHERE (split_part(split_part(TRIM(baseline.query_text),''}'',1),''"'', 4) IS NOT NULL 
    AND split_part(split_part(TRIM(target.query_text),''}'',1),''"'', 4) IS NOT NULL)
 )WITH NO SCHEMA BINDING;';
 RAISE INFO 'my_sql - > %', my_sql;
 EXECUTE my_sql;
END;
$$
LANGUAGE plpgsql;

Call the store procedure by passing the baseline and target parameters with the same values as the cluster_identifier of S3. In our example, we passed the cluster identifier of the baseline and producer clusters as the parameter values.

In [0]:
call common_queries_sp('baseline-ra3-4xlarge-2','producer-serverless32RPU');

Overall workload by user

In [0]:
SELECT username,count(*) FROM
common_queries
GROUP BY username
ORDER BY 2 desc;

Overall workload by query type

In [0]:
SELECT query_type,count(*) FROM
common_queries
GROUP BY query_type
ORDER BY 2 desc;

Overall workload comparison (in seconds)

In [0]:
SELECT 
SUM(baseline_query)/(1000000) baseline_elapsed_time, 
SUM(baseline_exec)/(1000000) baseline_execution_time,
SUM(baseline_compile)/(1000000) baseline_compile_time,
SUM(target_query)/(1000000) target_elapsed_time, 
SUM(target_exec)/(1000000) target_execution_time,
SUM(target_compile)/(1000000) target_compile_time
FROM common_queries

Percentile workload comparison

In [0]:
SELECT
ROUND(PERCENTILE_CONT (0.10) WITHIN GROUP(ORDER BY baseline_query),2)/(1000*1000) AS p10_s,
ROUND(PERCENTILE_CONT (0.20) WITHIN GROUP(ORDER BY baseline_query),2)/(1000*1000) AS p20_s,
ROUND(PERCENTILE_CONT (0.30) WITHIN GROUP(ORDER BY baseline_query),2)/(1000*1000) AS p30_s,
ROUND(PERCENTILE_CONT (0.40) WITHIN GROUP(ORDER BY baseline_query),2)/(1000*1000) AS p40_s,
ROUND(PERCENTILE_CONT (0.50) WITHIN GROUP(ORDER BY baseline_query),2)/(1000*1000) AS p50_s,
ROUND(PERCENTILE_CONT (0.60) WITHIN GROUP(ORDER BY baseline_query),2)/(1000*1000) AS p60_s,
ROUND(PERCENTILE_CONT (0.70) WITHIN GROUP(ORDER BY baseline_query),2)/(1000*1000) AS p70_s,
ROUND(PERCENTILE_CONT (0.80) WITHIN GROUP(ORDER BY baseline_query),2)/(1000*1000) AS p80_s,
ROUND(PERCENTILE_CONT (0.90) WITHIN GROUP(ORDER BY baseline_query),2)/(1000*1000) AS p90_s,
ROUND(PERCENTILE_CONT (0.99) WITHIN GROUP(ORDER BY baseline_query),2)/(1000*1000) AS p99_s,
ROUND(max(baseline_query)/(1000*1000),2) AS p_max
FROM common_queries;
SELECT 
ROUND(PERCENTILE_CONT (0.10) WITHIN GROUP(ORDER BY target_query::BIGINT),2)/(1000*1000) AS p10_s,
ROUND(PERCENTILE_CONT (0.20) WITHIN GROUP(ORDER BY target_query::BIGINT),2)/(1000*1000) AS p20_s,
ROUND(PERCENTILE_CONT (0.30) WITHIN GROUP(ORDER BY target_query::BIGINT),2)/(1000*1000) AS p30_s,
ROUND(PERCENTILE_CONT (0.40) WITHIN GROUP(ORDER BY target_query::BIGINT),2)/(1000*1000) AS p40_s,
ROUND(PERCENTILE_CONT (0.50) WITHIN GROUP(ORDER BY target_query::BIGINT),2)/(1000*1000) AS p50_s,
ROUND(PERCENTILE_CONT (0.60) WITHIN GROUP(ORDER BY target_query::BIGINT),2)/(1000*1000) AS p60_s,
ROUND(PERCENTILE_CONT (0.70) WITHIN GROUP(ORDER BY target_query::BIGINT),2)/(1000*1000) AS p70_s,
ROUND(PERCENTILE_CONT (0.80) WITHIN GROUP(ORDER BY target_query::BIGINT),2)/(1000*1000) AS p80_s,
ROUND(PERCENTILE_CONT (0.90) WITHIN GROUP(ORDER BY target_query::BIGINT),2)/(1000*1000) AS p90_s,
ROUND(PERCENTILE_CONT (0.99) WITHIN GROUP(ORDER BY target_query::BIGINT),2)/(1000*1000) AS p99_s,
ROUND(max(target_query::BIGINT)/(1000*1000),2) AS p_max
FROM common_queries;

Number of improve/degrade/stay same queries

In [0]:
SELECT 
SUM(CASE WHEN ROUND(((baseline_query::DECIMAL-target_query::DECIMAL)/baseline_query::DECIMAL),2) < 0 THEN 1 ELSE 0 END) as degrade,
SUM(CASE WHEN ROUND(((baseline_query::DECIMAL-target_query::DECIMAL)/baseline_query::DECIMAL),2) = 0 THEN 1 ELSE 0 END) as same,
SUM(CASE WHEN ROUND(((baseline_query::DECIMAL-target_query::DECIMAL)/baseline_query::DECIMAL),2) > 0 THEN 1 ELSE 0 END) as improve
FROM common_queries;

Degree of query-level performance change (proportion)

In [0]:
SELECT 
COUNT(*),
SUM(CASE WHEN ROUND(((baseline_query::DECIMAL-target_query::DECIMAL)/baseline_query::DECIMAL),2) <= -1 THEN 1 ELSE 0 END) as degrade_double,
SUM(CASE WHEN ROUND(((baseline_query::DECIMAL-target_query::DECIMAL)/baseline_query::DECIMAL),2) > -1 AND
ROUND(((baseline_query::DECIMAL-target_query::DECIMAL)/baseline_query::DECIMAL),2) <= -0.5 
THEN 1 ELSE 0 END) as degrade_half,
SUM(CASE WHEN ROUND(((baseline_query::DECIMAL-target_query::DECIMAL)/baseline_query::DECIMAL),2) > -0.5 AND
ROUND(((baseline_query::DECIMAL-target_query::DECIMAL)/baseline_query::DECIMAL),2) < 0
THEN 1 ELSE 0 END) as degrade_less_half,
SUM(CASE WHEN ROUND(((baseline_query::DECIMAL-target_query::DECIMAL)/baseline_query::DECIMAL),2) = 0
THEN 1 ELSE 0 END) as same,
SUM(CASE WHEN ROUND(((baseline_query::DECIMAL-target_query::DECIMAL)/baseline_query::DECIMAL),2) > 0 AND
ROUND(((baseline_query::DECIMAL-target_query::DECIMAL)/baseline_query::DECIMAL),2) < 0.5
THEN 1 ELSE 0 END) as improve_less_half,
SUM(CASE WHEN ROUND(((baseline_query::DECIMAL-target_query::DECIMAL)/baseline_query::DECIMAL),2) >= 0.5 AND
ROUND(((baseline_query::DECIMAL-target_query::DECIMAL)/baseline_query::DECIMAL),2) < 1
THEN 1 ELSE 0 END) as improve_half,
SUM(CASE WHEN ROUND(((baseline_query::DECIMAL-target_query::DECIMAL)/baseline_query::DECIMAL),2) >= 1 THEN 1 ELSE 0 END) as improve_double
FROM common_queries;

Comparison by query type (in seconds)

In [0]:
SELECT query_type,round(SUM((baseline_query)/(1000*1000))) as baseline_elapsed_time, 
round(SUM((target_query)/(1000*1000))) as target_elapsed_time
FROM common_queries
GROUP BY query_type
ORDER BY 2 desc;

Top 10 slowest running queries (in seconds)

In [0]:
SELECT querytxt,round(baseline_query / (1000 * 1000), 2) as baseline_elapsed_time, 
round(target_query / (1000 * 1000), 2) as target_elapsed_time 
FROM common_queries
ORDER by 2 DESC
Limit 10;

Top 10 improved queries (in seconds)

In [0]:
SELECT (baseline_query-target_query)/(1000*1000) perfromance_difference_sec, 
baseline_query/(1000*1000) baseline_elpased_time, 
target_query/(1000*1000) target_elpased_time, querytxt 
FROM common_queries
ORDER BY 1 ASC
Limit 10;